In [1]:
import requests
import urllib3
import json
import csv
import os
import datetime

import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np

urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

In [2]:
pd.set_option('display.max_columns', 83)
pd.set_option('display.max_colwidth', 25)
pd.set_option('display.max_rows', None)
pd.set_option("display.precision", 2)
sns.set(rc={'figure.figsize':(12.7,8.27)})

In [4]:
cd = os.path.abspath(os.getcwd())
with open(f'{cd}/config.json') as f:
    data = json.load(f)

In [5]:
auth_url = "https://www.strava.com/oauth/token"
activites_url = "https://www.strava.com/api/v3/athlete/activities"
payload = data['payload']
res = requests.post(auth_url, data=payload, verify=False)
header = {'Authorization': 'Bearer ' + res.json()['access_token']}

my_activities = pd.DataFrame()
for page in range(1,99):
    my_dataset = requests.get(activites_url, headers=header, params={'per_page': 200, 'page': page}).json()
    my_dataframe = pd.json_normalize(my_dataset)
    my_activities = pd.concat([my_activities, my_dataframe], ignore_index=True)

In [6]:
my_activities

resource_state                      name  distance  moving_time  \
0                  2                Night Walk    2496.4         1669   
1                  2            Afternoon Walk    1300.5          923   
2                  2            Afternoon Walk    1626.9          979   
3                  2            Afternoon Walk     578.8          304   
4                  2              Morning Walk    1634.4          961   
5                  2          Morning Activity       0.0         1730   
6                  2            Afternoon Walk    6146.8         4654   
7                  2                 Lunch Run    9112.7         3265   
8                  2          Morning Activity       0.0         2162   
9                  2              Evening Walk    1095.3          666   
10                 2              Evening Walk    1039.7          645   
11                 2            Afternoon Walk    2774.6         1648   
12                 2          Morning Activity       0.0         1951   
13                 2        Afternoon Activity       0.0         6426   
14                 2            Afternoon Walk    2732.9         1749   
15                 2          Morning Activity       0.0         2126   
16                 2          Evening Activity       0.0         2593   
17                 2             Afternoon Run   13043.3         5031   
18                 2            Afternoon Walk    3128.0         2033   
19                 2                Lunch Walk    1229.4          809   
20                 2          Morning Activity       0.0         1958   
21                 2          Evening Activity       0.0         1259   
22                 2              Evening Walk    2954.9         1799   
23                 2            Afternoon Walk    2992.8         1952   
24                 2          Morning Activity       0.0         1988   
25                 2          Evening Activity       0.0          548   
26                 2             Afternoon Run    6652.2         2514   
27                 2          Morning Activity       0.0          836   
28                 2          Morning Activity       0.0         1437   
29                 2          Evening Activity       0.0          527   
30                 2            Afternoon Walk   10804.5         6602   
31                 2          Morning Activity       0.0         1961   
32                 2          Evening Activity       0.0         1200   
33                 2             Afternoon Run   11013.3         4037   
34                 2          Morning Activity       0.0         2154   
35                 2          Evening Activity       0.0          339   
36                 2            Afternoon Walk    5991.4         3911   
37                 2          Morning Activity       0.0         2422   
38                 2          Evening Activity       0.0          952   
39                 2        Afternoon Activity       0.0         2936   
40                 2          Morning Activity       0.0         2523   
41                 2              Evening Walk    1953.7         1275   
42                 2              Evening Walk    1915.0         1193   
43                 2                 Lunch Run   12082.2         4329   
44                 2          Morning Activity       0.0         1955   
45                 2              Evening Walk    3105.3         1905   
46                 2        Afternoon Activity       0.0          966   
47                 2            Afternoon Walk    3934.9         2131   
48                 2          Morning Activity       0.0         2035   
49                 2              Evening Walk    1761.7         1070   
50                 2          Evening Activity       0.0          888   
51                 2            Afternoon Walk    2921.2         1713   
52                 2          Morning Activity       0.0         2195   
53                 2                 Lunch Run   16148.0        

In [31]:
with open(f'{cd}/csvs/raw/all_activities_raw.csv', 'w') as f:
    my_activities.to_csv(f)

In [44]:
runs_maps = my_activities[my_activities['type'] == 'Run'][['id', 'map.summary_polyline']]
walks_maps = my_activities[my_activities['type'] == 'Walk'][['id', 'map.summary_polyline']]

In [45]:
with open(f'{cd}/csvs/raw/runs_raw.csv', 'w') as runs_file, open(f'{cd}/csvs/raw/walks_raw.csv', 'w') as walks_file:
    runs_maps.to_csv(runs_file)
    walks_maps.to_csv(walks_file)

In [46]:
runs_maps = runs_maps.dropna()
walks_maps = walks_maps.dropna()

In [47]:
with open(f'{cd}/csvs/clean/runs.csv', 'w') as runs_file, open(f'{cd}/csvs/clean/walks.csv', 'w') as walks_file:
    runs_maps.to_csv(runs_file)
    walks_maps.to_csv(walks_file)

In [48]:
my_acts = my_activities.copy(deep=True)

In [49]:
my_acts = my_acts.rename(columns={'average_speed' : 'average_speed_mps', 
                                        'max_speed' : 'max_speed_mps',
                                        'moving_time' : 'moving_time_s',
                                        'elapsed_time' : 'elapsed_time_s'})

# fix 'start_date_local' and create 2 new columns 'start_time' and 'moving_time(min)'
my_acts['start_date_local'] = pd.to_datetime(my_acts['start_date_local'])
my_acts['start_time'] = my_acts['start_date_local'].dt.time
my_acts['start_date_local'] = my_acts['start_date_local'].dt.strftime("%d/%m/%y")

# seconds to minutes
my_acts['moving_time(min)'] = my_acts['moving_time_s'].apply(lambda x: pd.to_datetime(x, unit='s').strftime('%H:%M:%S'))

# meters to kms
my_acts['distance'] = my_acts[
    (my_acts['type'] == 'Run') |
    (my_acts['type'] == 'Walk')]['distance'] / 1000

# meters per second to kms per hour
my_acts['average_speed_mps'] = my_acts['average_speed_mps'] * (18/5)
my_acts['max_speed_mps'] = my_acts['max_speed_mps'] * (18/5)

# from (GMT+01:00) Europe/Berlin -> Europe/Berlin
my_acts['timezone'] = my_acts['timezone'].str.split(' ').str[-1]

# rename converted columns
my_acts = my_acts.rename(columns={'average_speed_mps': 'average_speed_kmh',
                                        'max_speed_mps' : 'max_speed_kmh',
                                        'distance' : 'distance_km'})

In [50]:
cols = ['upload_id', 'name', 'type', 'distance_km', 'moving_time(min)','start_time',  'start_date_local',  'timezone',
        'average_speed_kmh', 'max_speed_kmh', 'total_elevation_gain', 'average_heartrate',
        'max_heartrate', 'achievement_count', 'kudos_count', 'visibility',  ]
my_acts = my_acts[cols]

# usage -> 25.1 KB to 22.6 KB
my_acts['visibility'] = pd.Categorical(my_acts['visibility'])
my_acts['timezone'] = pd.Categorical(my_acts['timezone'])

In [51]:
my_acts

upload_id                      name            type  distance_km  \
0     6577437561                Night Walk            Walk         2.50   
1     6577437527            Afternoon Walk            Walk         1.30   
2     6577437506            Afternoon Walk            Walk         1.63   
3     6577437473            Afternoon Walk            Walk         0.58   
4     6577437465              Morning Walk            Walk         1.63   
5     6577437400          Morning Activity         Workout          NaN   
6     6571511144            Afternoon Walk            Walk         6.15   
7     6569703249                 Lunch Run             Run         9.11   
8     6569703133          Morning Activity         Workout          NaN   
9     6567619763              Evening Walk            Walk         1.10   
10    6567619739              Evening Walk            Walk         1.04   
11    6567619727            Afternoon Walk            Walk         2.77   
12    6567619646          Morning Activity         Workout          NaN   
13    6562611561        Afternoon Activity         Workout          NaN   
14    6562611521            Afternoon Walk            Walk         2.73   
15    6562611453          Morning Activity         Workout          NaN   
16    6562611313          Evening Activity         Workout          NaN   
17    6556786134             Afternoon Run             Run        13.04   
18    6555856136            Afternoon Walk            Walk         3.13   
19    6555855982                Lunch Walk            Walk         1.23   
20    6555855950          Morning Activity         Workout          NaN   
21    6552546026          Evening Activity  WeightTraining          NaN   
22    6552546031              Evening Walk            Walk         2.95   
23    6552545988            Afternoon Walk            Walk         2.99   
24    6552545924          Morning Activity         Workout          NaN   
25    6548059887          Evening Activity  WeightTraining          NaN   
26    6545829298             Afternoon Run             Run         6.65   
27    6545832819          Morning Activity         Workout          NaN   
28    6545832700          Morning Activity         Workout          NaN   
29    6545832466          Evening Activity  WeightTraining          NaN   
30    6542019196            Afternoon Walk            Walk        10.80   
31    6542018840          Morning Activity         Workout          NaN   
32    6542018763          Evening Activity         Workout          NaN   
33    6535717805             Afternoon Run             Run        11.01   
34    6535717678          Morning Activity         Workout          NaN   
35    6532152752          Evening Activity  WeightTraining          NaN   
36    6532152766            Afternoon Walk            Walk         5.99   
37    6529540333          Morning Activity         Workout          NaN   
38    6527264017          Evening Activity  WeightTraining          NaN   
39    6527263981        Afternoon Activity         Workout          NaN   
40    6524445677          Morning Activity         Workout          NaN   
41    6524445633              Evening Walk            Walk         1.95   
42    6524445606              Evening Walk            Walk         1.92   
43    6520128557                 Lunch Run             Run        12.08   
44    6520128360          Morning Activity         Workout          NaN   
45    6516709935              Evening Walk            Walk         3.11   
46    6516709853        Afternoon Activity  WeightTraining          NaN   
47    6516709848            Afternoon Walk            Walk         3.93   
48    6516709726          Morning Activity         Workout          NaN   
49    6512527184              Evening Walk            Walk         1.76   
50    6512527139          Evening Activity  WeightTraining          NaN   
51    6512527114            Afternoon Walk            Walk         2.92   
52    6512527052          Mornin

In [52]:
with open(f'{cd}/csvs/clean/all_activities.csv', 'w') as activs_f:
    my_acts.to_csv(activs_f)

In [53]:
with open(f'{cd}/csvs/clean/all_activities.csv', 'r') as activs_f:
    activities = pd.read_csv(activs_f, delimiter=',' , encoding='iso-8859-1', index_col=[0])

In [54]:
activities.shape

(1095, 16)

 IDEAS
 check the name: 'run'-> move to a new df['running']
                'other' -> df['rest_sessions']
activities

In [ ]:
activities['type'].value_counts().plot(kind='bar', rot=30).set_title("Each activity's # of occurences")

In [ ]:
sns.countplot(x='type',
              data=activities)

In [ ]:
run = activities.loc[activities['type'] == 'Run']

In [ ]:
run.shape

In [ ]:
sns.countplot(x='name', 
              data=run, 
              order=pd.value_counts(run['name']).iloc[:4].index)
locs, labels = plt.xticks(rotation=45, fontsize=8)
plt.title("Different named runs and their couns")
plt.xlabel("Name of run")
plt.ylabel("Count")

In [ ]:
run_5_more = run[run['distance_km'] > 5]

In [ ]:
sns.scatterplot(x='distance_km',
                y='moving_time(min)',
                data=run_5_more)
locs,label = plt.xticks(rotation=90, fontsize=3)

In [ ]:
sns.set(style="ticks", context="talk")
sns.regplot(x="distance_km", y="average_speed_kmh", data=run).set_title("Average Speed vs Distance")

In [ ]:
sns.set(style="ticks", context="talk")
sns.regplot(x='distance_km', y='max_speed_kmh', data=run).set_title("Max Speed vs Distance")

In [ ]:
sns.boxplot(x='name',y='distance_km',data=run_5_more)
locs, labels = plt.xticks(rotation=45, fontsize=12)

In [ ]:
sns.displot(run['distance_km'])